### v2 - use list of predictions from stage 1 model

In [2]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [3]:
!pip install catboost shap

     |████████████████████████████████| 65.8MB 46kB/s 
     |████████████████████████████████| 327kB 53.9MB/s 
  Created wheel for shap: filename=shap-0.37.0-cp36-cp36m-linux_x86_64.whl size=463917 sha256=58eaf974d0b0a0e58d2eec27a92061c1edc9eba802434c5a94f36b9cf2b9fcba
  Stored in directory: /root/.cache/pip/wheels/df/ad/b0/aa7815ec68850d66551ef618095eccb962c8f6022f1d3dd989
Successfully built shap


In [4]:
from catboost import Pool, cv, CatBoostClassifier, CatBoostRegressor,CatBoost
from sklearn.metrics import roc_auc_score, classification_report
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split

import gc
import matplotlib.pyplot as plt

from sklearn import metrics
import shap
import gc
from copy import deepcopy
from sklearn.preprocessing import LabelEncoder, StandardScaler, MinMaxScaler, OrdinalEncoder
import pandas as pd
from sklearn.model_selection import train_test_split, GroupShuffleSplit, GridSearchCV
import numpy as np
from tensorflow.keras.metrics import TopKCategoricalAccuracy, Precision, SparseTopKCategoricalAccuracy # @4
from tensorflow.keras.utils import to_categorical
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import layers

from sklearn.linear_model import  LogisticRegressionCV
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import StandardScaler, OneHotEncoder

%matplotlib inline

pd.set_option("display.max_columns", 90)

In [5]:
!nvidia-smi -L

GPU 0: Tesla P4 (UUID: GPU-60de6523-4efa-0ab1-8c38-1603143eeea7)


In [6]:
# ## https://www.tensorflow.org/guide/mixed_precision ## TF mixed precision - pytorch requires other setup
# from tensorflow.keras.mixed_precision import experimental as mixed_precision

# policy = mixed_precision.Policy('mixed_float16')
# mixed_precision.set_policy(policy)
# ## will need to correct in places, e.g.: 
# ## outputs = layers.Activation('softmax', dtype='float32', name='predictions')(x)

#### Features to add:
* Lag 
* Rank (popularity) of city, country (in general, +- given booker country)
* Count of hotel; user, trip size ? (may be leaky )
* Seasonal features - Holidays? , datetime

Aggregate feats:
* user changed country? last booking (lag 1) country change? 
* max/min/avg popularity rank of previous locations visited



We should create a dictionary of the rank, count, city/country etc' feats, so we can easily merge them when making more "negative" samples/feats for ranking.


* Consider using a df2 of df without dates + drop_duplicates, +- without user/trip id (After calcing that) .


Leaky or potentially leaky (Dependso n test set): 
* Target freq features - frequency of target city, given source county +- affiliate +- month of year +- given country (and interactions of target freq). 
    * Risk of leaks - depends of test data has temporal split or not. 
    * cartboost can do target encode, but this lets us do it for interactions, e.g. target city freq given the 2 countries and affiliate.
    * beware overfitting! 

In [7]:
# MIN_TARGET_FREQ = 40 # drop target/city_id values that appear less than this many times, as final step's target 
# KEEP_TOP_K_TARGETS = 2000 # keep K most frequent city ID targets (redundnat with the above, )

## (some) categorical variables that appear less than this many times will be replaced with a placeholder value!
## Includes CITY id (but done after target filtering, to avoid creating a "rare class" target:
# LOW_COUNT_THRESH = 8

TARGET_COL = "label"
RUN_TABNET = False
max_epochs = 800

FASTRUN = True

In [8]:
# most basic categorical columns , without 'user_id', , 'utrip_id' ordevice_class - used for count encoding/filtering
BASE_CAT_COLS = ['city_id',  'affiliate_id', 'booker_country', 'hotel_country']

### features to get lags for. Not very robust. May want different feats for lags before -1
LAG_FEAT_COLS = ['city_id', 'device_class',
       'affiliate_id', 'booker_country', 'hotel_country', 
       'duration', 'same_country', 'checkin_weekday',
       'checkin_week',
        'checkout_weekday',
       'city_id_count', 'affiliate_id_count',
#        'booker_country_count',
                 'hotel_country_count', 
                 'checkin_week_count',
                 'city_id_rank_by_hotel_country',
       'city_id_rank_by_booker_country', 
                 'city_id_rank_by_affiliate',
       'affiliate_id_rank_by_hotel_country',
#        'affiliate_id_rank_by_booker_country', 
#        'booker_country_rank_by_hotel_country',
#        'booker_country_rank_by_booker_country',
#        'booker_country_rank_by_affiliate',
#        'hotel_country_rank_by_hotel_country',
       'hotel_country_rank_by_booker_country',
       'hotel_country_rank_by_affiliate',
#        'checkin_month_rank_by_hotel_country',
#        'checkin_month_rank_by_booker_country',
#        'checkin_month_rank_by_affiliate'
                ]


CAT_FEAT_NAMES = ["booker_country", "device_class","affiliate_id",
"city_id","hotel_country",
"utrip_id",
#                   "user_id", ## ? could use lower dim - depends on train/test overlap
"checkin_week",#"checkout_week",
#                     "checkin_weekday",
"lag1_city_id","lag1_booker_country","lag1_hotel_country","lag1_affiliate_id", "lag1_device_class",
"lag2_city_id","lag2_booker_country","lag2_hotel_country","lag2_affiliate_id","lag2_device_class",
#       "lag3_city_id","lag3_booker_country","lag3_hotel_country","lag3_affiliate_id","lag3_device_class",
"first_hotel_country","first_city_id"
]

In [9]:
# https://stackoverflow.com/questions/33907537/groupby-and-lag-all-columns-of-a-dataframe
# https://stackoverflow.com/questions/62924987/lag-multiple-variables-grouped-by-columns
## lag features with groupby over many columns: 
def groupbyLagFeatures(df:pd.DataFrame,lag:[]=[1,2],group="utrip_id",lag_feature_cols=[]):
    """
    lag features with groupby over many columns
    https://stackoverflow.com/questions/62924987/lag-multiple-variables-grouped-by-columns"""
    if len(lag_feature_cols)>0:
        df=pd.concat([df]+[df.groupby(group)[lag_feature_cols].shift(x).add_prefix('lag'+str(x)+"_") for x in lag],axis=1)
    else:
         df=pd.concat([df]+[df.groupby(group).shift(x).add_prefix('lag'+str(x)+"_") for x in lag],axis=1)
    return df

def groupbyFirstLagFeatures(df:pd.DataFrame,group="user_id",lag_feature_cols=[]):
    """
    Get  first/head value lag-like of features with groupby over columns. Assumes sorted data!
    """
    if len(lag_feature_cols)>0:
        df=pd.concat([df]+[df.groupby(group)[lag_feature_cols].transform("first").add_prefix("first_")],axis=1)
    else:
#          df=pd.concat([df]+[df.groupby(group).first().add_prefix("first_")],axis=1)
        df=pd.concat([df]+[df.groupby(group).transform("first").add_prefix("first_")],axis=1)
    return df

######## Get n most popular items, per group
def most_popular(group, n_max=4):
    """Find most popular hotel clusters by destination
    Define a function to get most popular hotels for a destination group.

    Previous version used nlargest() Series method to get indices of largest elements. But the method is rather slow.
    Source: https://www.kaggle.com/dvasyukova/predict-hotel-type-with-pandas
    """
    relevance = group['relevance'].values
    hotel_cluster = group['hotel_cluster'].values
    most_popular = hotel_cluster[np.argsort(relevance)[::-1]][:n_max]
    return np.array_str(most_popular)[1:-1] # remove square brackets

from tensorflow.keras.metrics import top_k_categorical_accuracy
def top_4_accuracy(y_true, y_pred):
    """will only work if doing multiclass predictions"""
    return top_k_categorical_accuracy(y_true, y_pred, k=4)

## https://codereview.stackexchange.com/questions/149306/select-the-n-most-frequent-items-from-a-pandas-groupby-dataframe
# https://stackoverflow.com/questions/52073054/group-by-a-column-to-find-the-most-frequent-value-in-another-column
## can get modes (sorted)
# https://stackoverflow.com/questions/50592762/finding-most-common-values-with-pandas-groupby-and-value-counts
## df.groupby('tag')['category'].agg(lambda x: x.value_counts().index[0])
# https://stackoverflow.com/questions/15222754/groupby-pandas-dataframe-and-select-most-common-value
# source2.groupby(['Country','City'])['Short name'].agg(pd.Series.mode)


In [10]:
dtypes_dict = {
#     "utrip_id":"category",
    "city_id":"int32",
    "rank":"int16",
    "label":"int8",
    "affiliate_id":"int32",
#     "device_class":"category",
#     "booker_country":"string", ## category would save more memory but intereferes with feature engineering
#     "hotel_country":"string"
}

In [11]:
TRAIN_FILE_PATH = "/content/drive/MyDrive/booking_wisdom/booking_train_set.csv" #"booking_train_set.csv"
LIST_FILE_PATH = "/content/drive/MyDrive/booking_wisdom/list_booking_train.csv.gz" #"list_booking_train.csv.gz"

In [12]:
if FASTRUN:
    df = pd.read_csv(TRAIN_FILE_PATH,
                     nrows=200_000,
                     index_col=[0],
                     parse_dates=["checkin","checkout"],infer_datetime_format=True, dtype=dtypes_dict)
else:
    df = pd.read_csv(TRAIN_FILE_PATH,
                     index_col=[0],
                     parse_dates=["checkin","checkout"],infer_datetime_format=True, dtype=dtypes_dict)

## list of candidate predictions (100 per utrip_id)
df_list = pd.read_csv(LIST_FILE_PATH,
                        usecols=[0,2,3], # skip city_id col
                        dtype=dtypes_dict)
print("rank of labels (target =1):")
print(df_list.loc[df_list["label"]==1]["rank"].describe())

df_list.set_index("utrip_id",inplace=True)

# # ## HACK due to running out of mempory ! 
# df_list = df_list.loc[df_list["rank"]<=33]    

if FASTRUN:
    df_list = df_list.loc[(df_list["rank"]<=40) | (df_list["label"]==1)]    

df.sort_values(["user_id","checkin"],inplace=True)
# df_list.set_index("utrip_id",inplace=True)
display(df)
display(df_list)

rank of labels (target =1):
count    191671.000000
mean         11.927016
std          18.841272
min           0.000000
25%           1.000000
50%           4.000000
75%          14.000000
max          99.000000
Name: rank, dtype: float64


user_id    checkin   checkout  city_id device_class  affiliate_id  \
117277      136 2016-09-20 2016-09-22    52933      desktop          9924   
117278      136 2016-09-22 2016-09-23    51685      desktop          9924   
117279      136 2016-09-23 2016-09-24    43323      desktop          9924   
117280      136 2016-09-24 2016-09-26    55990      desktop          9924   
117281      136 2016-09-26 2016-09-27    46411      desktop          9924   
...         ...        ...        ...      ...          ...           ...   
64260   6257973 2016-08-12 2016-08-15    15470       tablet          5755   
180788  6258041 2016-04-28 2016-04-29    57109       mobile          9452   
180789  6258041 2016-04-29 2016-04-30    57109       mobile          9452   
180790  6258041 2016-04-30 2016-05-01     7529       mobile          9452   
180791  6258041 2016-05-01 2016-05-02    17338       mobile          9452   

              booker_country hotel_country   utrip_id  
117277  The Devilfire Empire     Osterlich      136_4  
117278  The Devilfire Empire     Osterlich      136_4  
117279  The Devilfire Empire     Osterlich      136_4  
117280  The Devilfire Empire     Osterlich      136_4  
117281  The Devilfire Empire     Osterlich      136_4  
...                      ...           ...        ...  
64260                 Gondal      Rolisica  6257973_1  
180788               Elbonia  Glubbdubdrib  6258041_1  
180789               Elbonia  Glubbdubdrib  6258041_1  
180790               Elbonia  Glubbdubdrib  6258041_1  
180791               Elbonia  Glubbdubdrib  6258041_1  

[200000 rows x 9 columns]

rank  label
utrip_id              
727105_1      0      0
727105_1      1      0
727105_1      2      0
727105_1      3      0
727105_1      4      0
...         ...    ...
2730109_1    36      0
2730109_1    37      0
2730109_1    38      0
2730109_1    39      0
2730109_1    40      0

[8350752 rows x 2 columns]

In [13]:
df["duration"] = ((df["checkout"] - df["checkin"]).dt.days).astype(int)
df["same_country"] = (df["booker_country"]==df["hotel_country"]).astype(int)

df["checkin_day"] = df["checkin"].dt.day
df["checkin_weekday"] = df["checkin"].dt.weekday
df["checkin_week"] = df["checkin"].dt.isocalendar().week.astype(int) ## week of year
df["checkin_month"] = df["checkin"].dt.month
df["checkin_year"] = df["checkin"].dt.year-2015
df["checkin_day_of_year"] = df["checkin"].dt.dayofyear  # day of year - may overfit , but will allow learning holidays and other checkins on that date 

df["checkin_quarter"] = df["checkin"].dt.quarter # relatively redundant but may be used for "id"

df["checkout_weekday"] = df["checkout"].dt.weekday
df["checkout_week"] = df["checkout"].dt.isocalendar().week.astype(int) ## week of year
df["checkout_day"] = df["checkout"].dt.day ## day of month

## cyclical datetime embeddings
## drop originakl variables? 
## TODO:L add for other variables, +- those that we'll embed (week?)

# df['checkin_weekday_sin'] = np.sin(df["checkin_weekday"]*(2.*np.pi/7))
# df['checkin_weekday_cos'] = np.cos(df["checkin_weekday"]*(2.*np.pi/7))

df['checkin_month_sin'] = np.sin((df["checkin_month"]-1)*(2.*np.pi/12))
df['checkin_month_cos'] = np.cos((df["checkin_month"]-1)*(2.*np.pi/12))

df['checkin_week_sin'] = np.sin((df["checkin_week"]-1)*(2.*np.pi/53))
df['checkin_week_cos'] = np.cos((df["checkin_week"]-1)*(2.*np.pi/53))

# #############
# # last number in utrip id - probably which trip number it is:
# df["utrip_number"] = df["utrip_id"].str.split("_",expand=True)[1].astype(int)

### encode string columns - must be consistent with test data 
### IF we can concat test with train, we can just do a single transformation  for the NON TARGET cols
# obj_cols_list = df.select_dtypes("O").columns.values
obj_cols_list = ['device_class','booker_country','hotel_country'] # we could also define when loading data, dtype

# for c in obj_cols_list:
#     df[c] = df[c].astype("category")
#     df[c] = df[c].cat.codes.astype(int)


## view steps of a trip per user & trip, in order. ## last step == 1.
## count #/pct step in a trip (utrip_id) per user. Useful to get the "final" step per trip - for prediction
## note that the order is ascending, so we would need to select by "last" . (i.e "1" is the first step, 2 the second, etc') , or we could use pct .rank(ascending=True,pct=True)
#### this feature overlaps with the count of each trip id (for the final row)
##  = df.sort_values(["checkin","checkout"])... - df already sorted above
# df["utrip_steps_from_end"] = df.groupby("utrip_id")["checkin"].rank(ascending=True,pct=True) #.cumcount("user_id")


In [14]:
### add features to be consistent with test set of row in trip, and total trips in trip
df["row_num"] = df.groupby("utrip_id")["checkin"].rank(ascending=True,pct=False).astype(int)
utrip_counts = df["utrip_id"].value_counts()
df["total_rows"] = df["utrip_id"].map(utrip_counts)

df[["row_num","total_rows"]].describe()

row_num     total_rows
count  200000.000000  200000.000000
mean        3.551565       6.103130
std         2.372298       2.796659
min         1.000000       1.000000
25%         2.000000       4.000000
50%         3.000000       5.000000
75%         5.000000       7.000000
max        48.000000      48.000000

In [15]:
df["last"] = (df["row_num"] ==df["total_rows"]).astype(int)

* Add first country, city visited in a trip. 
* Drop first row of a trip

In [16]:
## add the "first" place visited/values
### nopte - will need to drop first row in trip, or impute nans when using this feature 

### first by user results in too much sparsity/rareness for our IDs purposes
df = groupbyFirstLagFeatures(df,group="utrip_id",lag_feature_cols=["hotel_country","city_id","duration","same_country"]) # ["hotel_country","city_id"]

# df = df.loc[df["row_num"]>1] ## can't do yet, needed for lag features
print(df[["first_hotel_country","hotel_country","city_id"]].nunique())
df


first_hotel_country      141
hotel_country            162
city_id                20148
dtype: int64


user_id    checkin   checkout  city_id device_class  affiliate_id  \
117277      136 2016-09-20 2016-09-22    52933      desktop          9924   
117278      136 2016-09-22 2016-09-23    51685      desktop          9924   
117279      136 2016-09-23 2016-09-24    43323      desktop          9924   
117280      136 2016-09-24 2016-09-26    55990      desktop          9924   
117281      136 2016-09-26 2016-09-27    46411      desktop          9924   
...         ...        ...        ...      ...          ...           ...   
64260   6257973 2016-08-12 2016-08-15    15470       tablet          5755   
180788  6258041 2016-04-28 2016-04-29    57109       mobile          9452   
180789  6258041 2016-04-29 2016-04-30    57109       mobile          9452   
180790  6258041 2016-04-30 2016-05-01     7529       mobile          9452   
180791  6258041 2016-05-01 2016-05-02    17338       mobile          9452   

              booker_country hotel_country   utrip_id  duration  same_country  \
117277  The Devilfire Empire     Osterlich      136_4         2             0   
117278  The Devilfire Empire     Osterlich      136_4         1             0   
117279  The Devilfire Empire     Osterlich      136_4         1             0   
117280  The Devilfire Empire     Osterlich      136_4         2             0   
117281  The Devilfire Empire     Osterlich      136_4         1             0   
...                      ...           ...        ...       ...           ...   
64260                 Gondal      Rolisica  6257973_1         3             0   
180788               Elbonia  Glubbdubdrib  6258041_1         1             0   
180789               Elbonia  Glubbdubdrib  6258041_1         1             0   
180790               Elbonia  Glubbdubdrib  6258041_1         1             0   
180791               Elbonia  Glubbdubdrib  6258041_1         1             0   

        checkin_day  checkin_weekday  checkin_week  checkin_month  \
117277           20                1            38              9   
117278           22                3            38              9   
117279           23                4            38              9   
117280           24                5            38              9   
117281           26                0            39              9   
...             ...              ...           ...            ...   
64260            12                4            32              8   
180788           28                3            17              4   
180789           29                4            17              4   
180790           30                5            17              4   
180791            1                6            17              5   

        checkin_year  checkin_day_of_year  checkin_quarter  checkout_weekday  \
117277             1                  264                3                 3   
117278             1                  266                3                 4   
117279             1                  267                3                 5   
117280             1                  268                3                 0   
117281             1                  270                3                 1   
...              ...                  ...              ...               ...   
64260              1                  225                3                 0   
180788             1                  119                2                 4   
180789             1                  120                2                 5   
180790             1                  121                2                 6   
180791             1                  122                2                 0   

        checkout_week  checkout_day  checkin_month_sin  checkin_month_cos  \
117277             38            22          -0.866025      -5.000000e-01   
117278             38            23          -0.866025      -5.000000e-01   
117279             38            24          -0.866025      -5.000000e-01   
117280      

In [17]:
### replace rare variables (under 2 occurrences) with "-1" dummy

affiliates_counts = df["affiliate_id"].value_counts()
print("before:", affiliates_counts)
print("uniques",df["affiliate_id"].nunique())
affiliates_counts = affiliates_counts.to_dict()
# df["affiliate_id"] = df["affiliate_id"].where(df["affiliate_id"].apply(lambda x: x.map(x.value_counts()))>=3, -1)
df["affiliate_id"] = df["affiliate_id"].where(df["affiliate_id"].map(affiliates_counts)>=3, -1)
df["affiliate_id"] = df["affiliate_id"].astype(int)

print("after\n",df["affiliate_id"].value_counts())
print("uniques",df["affiliate_id"].nunique())

before: 9924    47574
359     29601
384     15200
9452    14618
4541     7270
        ...  
1858        1
5696        1
3614        1
3699        1
4094        1
Name: affiliate_id, Length: 1589, dtype: int64
uniques 1589
after
 9924     47574
359      29601
384      15200
9452     14618
4541      7270
         ...  
10185        3
7467         3
8329         3
364          3
9113         3
Name: affiliate_id, Length: 974, dtype: int64
uniques 974


In [18]:
### for possible "user id" embedding/ID : How many unique values are there for these source tuple? :
### Could also maybe add previous location/lag1 country/city ? 
## 'device_class','affiliate_id', 'booker_country' - 7.5 K "uniques"
## 'device_class','affiliate_id', 'booker_country','checkin_month' - 24 K "uniques"
## 'device_class','affiliate_id', 'booker_country','checkin_quarter' 14K "uniques"

print(df[['device_class','affiliate_id', 'booker_country','checkin_month',"total_rows"]].nunique(axis=0))
df.groupby(['device_class','affiliate_id', 'booker_country','checkin_quarter']).size()

device_class        3
affiliate_id      974
booker_country      5
checkin_month      12
total_rows         29
dtype: int64


device_class  affiliate_id  booker_country  checkin_quarter
desktop       -1            Bartovia        2                   3
                                            3                  13
                                            4                  13
                            Elbonia         1                  22
                                            2                  32
                                                               ..
tablet         10582        Elbonia         2                   2
                                            3                   5
               10615        Elbonia         2                   2
                                            3                   5
               10668        Gondal          1                   1
Length: 5012, dtype: int64

In [19]:
##### Following aggregation features - would be best to use time window (sort data) to generate, otherwise they will LEAK! (e.g. nunique countries visited)

### count features (can also later add rank inside groups).
### Some may be leaks (# visits in a trip should use time window?) , and do users repeat? 
### can add more counts of group X time period (e.g. affiliate X month of year)
## alt way to get counts/freq :
# freq = df["city_id"].value_counts()
# df["city_id_count"] = df["city_id"].map(freq)
# print(df["city_id_count"].describe())

count_cols = [ 'city_id','affiliate_id',  'hotel_country', 
#               'utrip_id','user_id', 
 "checkin_month",
              "checkin_week"]
for c in count_cols:
    df[f"{c}_count"] = df.groupby([c])["duration"].transform("size")
    
########################################################
## nunique per trip
### https://stackoverflow.com/questions/46470743/how-to-efficiently-compute-a-rolling-unique-count-in-a-pandas-time-series

nunique_cols = [ 'city_id', 'hotel_country','affiliate_id', 'booker_country']
# df["nunique_booker_countries"] = df.groupby("utrip_id")["booker_country"].nunique()
# df["nunique_hotel_country"] = df.groupby("utrip_id")["hotel_country"].nunique()
for c in nunique_cols:
    df[f"{c}_nunique"] = df.groupby(["utrip_id"])[c].transform("nunique")
print(df.nunique())

########################################################
## get frequency/count feature's rank within a group - e.g. within a country (or affiliate) 
## add "_count" to column name to get count col name, then add rank col 

### ALT/ duplicate feat - add percent rank (instead or in addition)

rank_cols = ['city_id','affiliate_id', 'hotel_country',  # 'booker_country',
 "checkin_month"]
### what is meaning of groupby and rank of smae variable by same var? Surely should be 1 / unary? 
for c in rank_cols:
    df[f"{c}_rank_by_hotel_country"] = df.groupby(['hotel_country'])[f"{c}_count"].transform("rank")
    df[f"{c}_rank_by_booker_country"] = df.groupby(['booker_country'])[f"{c}_count"].transform("rank")
    df[f"{c}_rank_by_affiliate"] = df.groupby(['affiliate_id'])[f"{c}_count"].transform("rank")
    
df

user_id                   36694
checkin                     425
checkout                    425
city_id                   20148
device_class                  3
affiliate_id                974
booker_country                5
hotel_country               162
utrip_id                  37353
duration                     28
same_country                  2
checkin_day                  31
checkin_weekday               7
checkin_week                 53
checkin_month                12
checkin_year                  3
checkin_day_of_year         366
checkin_quarter               4
checkout_weekday              7
checkout_week                53
checkout_day                 31
checkin_month_sin            12
checkin_month_cos            12
checkin_week_sin             53
checkin_week_cos             45
row_num                      48
total_rows                   29
last                          2
first_hotel_country         141
first_city_id              7727
first_duration               23
first_sa

user_id    checkin   checkout  city_id device_class  affiliate_id  \
117277      136 2016-09-20 2016-09-22    52933      desktop          9924   
117278      136 2016-09-22 2016-09-23    51685      desktop          9924   
117279      136 2016-09-23 2016-09-24    43323      desktop          9924   
117280      136 2016-09-24 2016-09-26    55990      desktop          9924   
117281      136 2016-09-26 2016-09-27    46411      desktop          9924   
...         ...        ...        ...      ...          ...           ...   
64260   6257973 2016-08-12 2016-08-15    15470       tablet          5755   
180788  6258041 2016-04-28 2016-04-29    57109       mobile          9452   
180789  6258041 2016-04-29 2016-04-30    57109       mobile          9452   
180790  6258041 2016-04-30 2016-05-01     7529       mobile          9452   
180791  6258041 2016-05-01 2016-05-02    17338       mobile          9452   

              booker_country hotel_country   utrip_id  duration  same_country  \
117277  The Devilfire Empire     Osterlich      136_4         2             0   
117278  The Devilfire Empire     Osterlich      136_4         1             0   
117279  The Devilfire Empire     Osterlich      136_4         1             0   
117280  The Devilfire Empire     Osterlich      136_4         2             0   
117281  The Devilfire Empire     Osterlich      136_4         1             0   
...                      ...           ...        ...       ...           ...   
64260                 Gondal      Rolisica  6257973_1         3             0   
180788               Elbonia  Glubbdubdrib  6258041_1         1             0   
180789               Elbonia  Glubbdubdrib  6258041_1         1             0   
180790               Elbonia  Glubbdubdrib  6258041_1         1             0   
180791               Elbonia  Glubbdubdrib  6258041_1         1             0   

        checkin_day  checkin_weekday  checkin_week  checkin_month  \
117277           20                1            38              9   
117278           22                3            38              9   
117279           23                4            38              9   
117280           24                5            38              9   
117281           26                0            39              9   
...             ...              ...           ...            ...   
64260            12                4            32              8   
180788           28                3            17              4   
180789           29                4            17              4   
180790           30                5            17              4   
180791            1                6            17              5   

        checkin_year  checkin_day_of_year  checkin_quarter  checkout_weekday  \
117277             1                  264                3                 3   
117278             1                  266                3                 4   
117279             1                  267                3                 5   
117280             1                  268                3                 0   
117281             1                  270                3                 1   
...              ...                  ...              ...               ...   
64260              1                  225                3                 0   
180788             1                  119                2                 4   
180789             1                  120                2                 5   
180790             1                  121                2                 6   
180791             1                  122                2                 0   

        checkout_week  checkout_day  checkin_month_sin  checkin_month_cos  \
117277             38            22          -0.866025      -5.000000e-01   
117278             38            23          -0.866025      -5.000000e-01   
117279             38            24          -0.866025      -5.000000e-01   
117280      

#### DF of features per city
* We can join this to the list of candidate cities

WARNING! Some features here are NOT Calculate d correctly - we see too many values, they are not unique per city_id & hotel!! 

In [20]:
# CITY_FEATURES = df.columns[(df.columns.str.contains("city|hotel",case=False)) & (~df.columns.str.contains("first_|month",case=False))]
CITY_FEATURES = ['city_id', 'hotel_country', 'city_id_count', 'hotel_country_count',
       'city_id_rank_by_hotel_country']

print("city features\n",CITY_FEATURES)

df_city_features = df[CITY_FEATURES].drop_duplicates().set_index("city_id") 
assert df["city_id"].nunique() == df_city_features.shape[0]

print(df_city_features.shape)

city features
 ['city_id', 'hotel_country', 'city_id_count', 'hotel_country_count', 'city_id_rank_by_hotel_country']
(20148, 4)


In [21]:
df.loc[df["city_id_count"]>=10]["city_id"].nunique()

2650

In [22]:
assert df.isna().sum().max() ==0

In [23]:
df[[ 'checkin', 'checkout','booker_country', 'hotel_country', 'duration']].describe(include="all",datetime_is_numeric=True)

checkin                       checkout  \
count                          200000                         200000   
unique                            NaN                            NaN   
top                               NaN                            NaN   
freq                              NaN                            NaN   
mean    2016-08-02 02:20:29.615977984  2016-08-03 20:05:58.703989248   
min               2015-12-31 00:00:00            2016-01-01 00:00:00   
25%               2016-06-07 00:00:00            2016-06-09 00:00:00   
50%               2016-08-07 00:00:00            2016-08-08 00:00:00   
75%               2016-09-26 00:00:00            2016-09-28 00:00:00   
max               2017-02-27 00:00:00            2017-02-28 00:00:00   
std                               NaN                            NaN   

       booker_country hotel_country       duration  
count          200000        200000  200000.000000  
unique              5           162            NaN  
top            Gondal  Cobra Island            NaN  
freq            92328         23733            NaN  
mean              NaN           NaN       1.739920  
min               NaN           NaN       1.000000  
25%               NaN           NaN       1.000000  
50%               NaN           NaN       1.000000  
75%               NaN           NaN       2.000000  
max               NaN           NaN      30.000000  
std               NaN           NaN       1.210217

In [24]:
# LAG_FEAT_COLS = ['city_id', 'device_class',
#        'affiliate_id', 'booker_country', 'hotel_country', 
#        'duration', 'same_country', 'checkin_day', 'checkin_weekday',
#        'checkin_week',
#         'checkout_weekday','checkout_week',
#        'city_id_count', 'affiliate_id_count',
#        'booker_country_count', 'hotel_country_count', 
#        'checkin_month_count', 'checkin_week_count', 'city_id_nunique',
#        'affiliate_id_nunique', 'booker_country_nunique',
#        'hotel_country_nunique', 'city_id_rank_by_hotel_country',
#        'city_id_rank_by_booker_country', 'city_id_rank_by_affiliate',
#        'affiliate_id_rank_by_hotel_country',
#        'affiliate_id_rank_by_booker_country', 'affiliate_id_rank_by_affiliate',
#        'booker_country_rank_by_hotel_country',
#        'booker_country_rank_by_booker_country',
#        'booker_country_rank_by_affiliate',
#        'hotel_country_rank_by_hotel_country',
#        'hotel_country_rank_by_booker_country',
#        'hotel_country_rank_by_affiliate',
#        'checkin_month_rank_by_hotel_country',
#        'checkin_month_rank_by_booker_country',
#        'checkin_month_rank_by_affiliate']

### add lag features + Train/test/data split
* Lag feats (remember for categorical)
* Drop leak features (target values - country, city)

* drop instances  that lack history (e.g. at least 3d step and onwards) - by dropna in lag feat
* fill nans
* Split train/test by `user id` / split could maybe be by `utrip ID` ? ? 
    * Test - only last trip
    *  stratified train/test split by class - then drop any train rows with overlap with tests' IDs.  
        * Could also stratify by users, but risks some classes being non present in test
        
###### WE may not need to drop these features anymore - but we may want to join them by city id
* TODO: join city id by `hotel_country`  as feature

In [25]:
### features to drop - not usable, or leaks (e.g. aggregations on target)

DROP_FEATS = ['user_id',
    'checkin', 'checkout',
              'hotel_country',
              'city_id_count','same_country',
#               'utrip_id',
#               'utrip_steps_from_end',
             'city_id_count','hotel_country_count',
              'city_id_nunique', 'hotel_country_nunique',
              'city_id_rank_by_hotel_country','city_id_rank_by_booker_country', 'city_id_rank_by_affiliate',
              'affiliate_id_rank_by_hotel_country','affiliate_id_rank_by_booker_country', 'affiliate_id_rank_by_affiliate',
              'hotel_country_rank_by_hotel_country',
       'hotel_country_rank_by_booker_country','hotel_country_rank_by_affiliate',
              'booker_country_rank_by_hotel_country','booker_country_rank_by_booker_country',
              'checkin_month_rank_by_hotel_country',
             ]

# df2.drop(DROP_FEATS,axis=1).columns

In [26]:
df.columns

Index(['user_id', 'checkin', 'checkout', 'city_id', 'device_class',
       'affiliate_id', 'booker_country', 'hotel_country', 'utrip_id',
       'duration', 'same_country', 'checkin_day', 'checkin_weekday',
       'checkin_week', 'checkin_month', 'checkin_year', 'checkin_day_of_year',
       'checkin_quarter', 'checkout_weekday', 'checkout_week', 'checkout_day',
       'checkin_month_sin', 'checkin_month_cos', 'checkin_week_sin',
       'checkin_week_cos', 'row_num', 'total_rows', 'last',
       'first_hotel_country', 'first_city_id', 'first_duration',
       'first_same_country', 'city_id_count', 'affiliate_id_count',
       'hotel_country_count', 'checkin_month_count', 'checkin_week_count',
       'city_id_nunique', 'hotel_country_nunique', 'affiliate_id_nunique',
       'booker_country_nunique', 'city_id_rank_by_hotel_country',
       'city_id_rank_by_booker_country', 'city_id_rank_by_affiliate',
       'affiliate_id_rank_by_hotel_country',
       'affiliate_id_rank_by_booker_countr

In [27]:
print(df.shape)
# ### lag features - last n visits
df_feat = groupbyLagFeatures(df=df.copy(), 
                   lag=[1,2],group="utrip_id",lag_feature_cols=LAG_FEAT_COLS)
# df_feat = df_feat.dropna(subset=["lag2_city_id"]).sample(frac=1)
df_feat = df_feat.loc[df_feat["last"]==1]

# df_feat = df_feat.drop(DROP_FEATS,axis=1,errors="ignore")
print(df_feat.shape)

assert df_feat["utrip_id"].nunique() == df["utrip_id"].nunique()

### impute missing  values - for categoricals at least - strings, numbers
OBJECT_COLS = list(df_feat.select_dtypes("O").columns)
df_feat[OBJECT_COLS] = df_feat[OBJECT_COLS].fillna("")
df_feat[CAT_FEAT_NAMES] = df_feat[CAT_FEAT_NAMES].fillna(-1)
## maybe impute numerics? (for integer type, less data usage)

## downcast dtypes
df_feat = df_feat.apply(pd.to_numeric, errors='ignore',downcast="float").apply(pd.to_numeric, errors='ignore',downcast="integer")


df_feat = df_feat.apply(pd.to_numeric, errors='ignore',downcast="float").apply(pd.to_numeric, errors='ignore',downcast="integer")

# df_feat.sort_values(["user_id","utrip_steps_from_end"])
print(df_feat.info())
df_feat

(200000, 53)
(37353, 93)
<class 'pandas.core.frame.DataFrame'>
Int64Index: 37353 entries, 117283 to 180791
Data columns (total 93 columns):
 #   Column                                     Non-Null Count  Dtype  
---  ------                                     --------------  -----  
 0   user_id                                    37353 non-null  int32  
 1   checkin                                    37353 non-null  float32
 2   checkout                                   37353 non-null  float32
 3   city_id                                    37353 non-null  int32  
 4   device_class                               37353 non-null  object 
 5   affiliate_id                               37353 non-null  int16  
 6   booker_country                             37353 non-null  object 
 7   hotel_country                              37353 non-null  object 
 8   utrip_id                                   37353 non-null  object 
 9   duration                                   37353 non-null  int8

user_id       checkin      checkout  city_id device_class  \
117283      136  1.475021e+18  1.475107e+18    41113      desktop   
117413      149  1.486426e+18  1.486598e+18    28733      desktop   
163180      670  1.471046e+18  1.471478e+18      382      desktop   
29265       734  1.454026e+18  1.454198e+18    53962       mobile   
198786      854  1.480205e+18  1.480291e+18     5860       mobile   
...         ...           ...           ...      ...          ...   
151966  6257581  1.471392e+18  1.471478e+18    22175       mobile   
58384   6257694  1.463011e+18  1.463530e+18    36063      desktop   
98856   6257762  1.476058e+18  1.476230e+18    24912      desktop   
64260   6257973  1.470960e+18  1.471219e+18    15470       tablet   
180791  6258041  1.462061e+18  1.462147e+18    17338       mobile   

        affiliate_id        booker_country hotel_country   utrip_id  duration  \
117283          9924  The Devilfire Empire     Osterlich      136_4         1   
117413          5583  The Devilfire Empire        Kangan      149_1         2   
163180          9627                Gondal   Fook Island      670_2         5   
29265           2164           Tcherkistan       Aldovia      734_1         2   
198786          9452               Elbonia        Kangan      854_3         1   
...              ...                   ...           ...        ...       ...   
151966          4568                Gondal  Cobra Island  6257581_1         1   
58384           7974  The Devilfire Empire        Gondal  6257694_1         6   
98856           9924  The Devilfire Empire  Cobra Island  6257762_1         2   
64260           5755                Gondal      Rolisica  6257973_1         3   
180791          9452               Elbonia  Glubbdubdrib  6258041_1         1   

        same_country  checkin_day  checkin_weekday  checkin_week  \
117283             0           28                2            39   
117413             0            7                1             6   
163180             0           13                5            32   
29265              0           29                4             4   
198786             0           27                6            47   
...              ...          ...              ...           ...   
151966             0           17                2            33   
58384              0           12                3            19   
98856              0           10                0            41   
64260              0           12                4            32   
180791             0            1                6            17   

        checkin_month  checkin_year  checkin_day_of_year  checkin_quarter  \
117283              9             1                  272                3   
117413              2             2                   38                1   
163180              8             1                  226                3   
29265               1             1                   29                1   
198786             11             1                  332                4   
...               ...           ...                  ...              ...   
151966              8             1                  230                3   
58384               5             1                  133                2   
98856              10             1                  284                4   
64260               8             1                  225                3   
180791              5             1                  122                2   

        checkout_weekday  checkout_week  checkout_day  checkin_month_sin  \
117283                 3             39            29          -0.866025   
117413                 3              6             9           0.500000   
163180                 3             33            18          -0.500000   
29265                  6              4            31           0.000000   
198786                 0             48            28          -0.866025   
...     

### join with predicted candidates
* Note: be careful - features for the city/item must match the "new" city as well!! e.g. city rank


In [28]:
# df_feat =df_list.drop(["city_id"],axis=1,errors="ignore").merge(df_feat,how="inner",on="utrip_id")
df_feat =df_list.merge(df_feat,how="inner",on="utrip_id")
del( df_list)

print(df_feat.shape)
df_feat

(1433173, 95)


utrip_id  rank  label  user_id       checkin      checkout  city_id  \
0        3554942_1     0      0  3554942  1.451866e+18  1.451952e+18    20967   
1        3554942_1     1      0  3554942  1.451866e+18  1.451952e+18    20967   
2        3554942_1     2      0  3554942  1.451866e+18  1.451952e+18    20967   
3        3554942_1     3      0  3554942  1.451866e+18  1.451952e+18    20967   
4        3554942_1     4      0  3554942  1.451866e+18  1.451952e+18    20967   
...            ...   ...    ...      ...           ...           ...      ...   
1433168  2276261_2    36      0  2276261  1.487808e+18  1.487894e+18    39509   
1433169  2276261_2    37      0  2276261  1.487808e+18  1.487894e+18    39509   
1433170  2276261_2    38      0  2276261  1.487808e+18  1.487894e+18    39509   
1433171  2276261_2    39      0  2276261  1.487808e+18  1.487894e+18    39509   
1433172  2276261_2    40      0  2276261  1.487808e+18  1.487894e+18    39509   

        device_class  affiliate_id        booker_country hotel_country  \
0             mobile           359  The Devilfire Empire       Bozatta   
1             mobile           359  The Devilfire Empire       Bozatta   
2             mobile           359  The Devilfire Empire       Bozatta   
3             mobile           359  The Devilfire Empire       Bozatta   
4             mobile           359  The Devilfire Empire       Bozatta   
...              ...           ...                   ...           ...   
1433168      desktop           384                Gondal      Rolisica   
1433169      desktop           384                Gondal      Rolisica   
1433170      desktop           384                Gondal      Rolisica   
1433171      desktop           384                Gondal      Rolisica   
1433172      desktop           384                Gondal      Rolisica   

         duration  same_country  checkin_day  checkin_weekday  checkin_week  \
0               1             0            4                0             1   
1               1             0            4                0             1   
2               1             0            4                0             1   
3               1             0            4                0             1   
4               1             0            4                0             1   
...           ...           ...          ...              ...           ...   
1433168         1             0           23                3             8   
1433169         1             0           23                3             8   
1433170         1             0           23                3             8   
1433171         1             0           23                3             8   
1433172         1             0           23                3             8   

         checkin_month  checkin_year  checkin_day_of_year  checkin_quarter  \
0                    1             1                    4                1   
1                    1             1                    4                1   
2                    1             1                    4                1   
3                    1             1                    4                1   
4                    1             1                    4                1   
...                ...           ...                  ...              ...   
1433168              2             2                   54                1   
1433169              2             2                   54                1   
1433170              2             2                   54                1   
1433171              2             2                   54                1   
1433172              2             2                   54                1   

         checkout_weekday  checkout_week  checkout_day  checkin_month_sin  \
0                       1              1             5                0.0   
1                       1              1             5                0.0   
2                       1      

In [29]:
%%time
# df_feat = df_feat.apply(pd.to_numeric, errors='ignore',downcast="float").apply(pd.to_numeric, errors='ignore',downcast="integer")
df_feat.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1433173 entries, 0 to 1433172
Data columns (total 95 columns):
 #   Column                                     Non-Null Count    Dtype  
---  ------                                     --------------    -----  
 0   utrip_id                                   1433173 non-null  object 
 1   rank                                       1433173 non-null  int16  
 2   label                                      1433173 non-null  int8   
 3   user_id                                    1433173 non-null  int32  
 4   checkin                                    1433173 non-null  float32
 5   checkout                                   1433173 non-null  float32
 6   city_id                                    1433173 non-null  int32  
 7   device_class                               1433173 non-null  object 
 8   affiliate_id                               1433173 non-null  int16  
 9   booker_country                             1433173 non-null  object 

In [30]:
########################
## stratified train/test split by user or utrip_id
### split could maybe be by utrip ID ? 
### orig - split by group : 

train_inds, test_inds = next(GroupShuffleSplit(test_size=.2, n_splits=2, random_state = 7).split(df_feat, groups=df_feat['user_id']))

X_train = df_feat.iloc[train_inds].drop(DROP_FEATS,axis=1,errors="ignore").merge(df_city_features,on="city_id",how="left")
X_test = df_feat.iloc[test_inds].drop(DROP_FEATS,axis=1,errors="ignore").merge(df_city_features,on="city_id",how="left")

# df_feat.drop(['user_id'],axis=1,errors="ignore",inplace=True)
df_feat = df_feat.drop(DROP_FEATS,axis=1,errors="ignore")

df_feat = df_feat.merge(df_city_features,on="city_id",how="left")
df_feat.tail()

y_train = X_train.pop(TARGET_COL)
y_test = X_test.pop(TARGET_COL)

print("# classes",y_train.nunique())

# ## check that same classes in train and test - 
# assert (set(y_train.unique()) == set(y_test.unique()))
assert y_train.isna().max() == y_test.isna().max() == 0

# classes 2


## Model
* For now - simple multiclass model (Tabnet? LSTM?) ; +- subsample - only most frequent classes/cities

    * Tabnet: `pip install pytorch-tabnet`
        * https://github.com/dreamquark-ai/tabnet/blob/develop/forest_example.ipynb
    * TensorFlow Tabmet: https://github.com/ostamand/tensorflow-tabnet/blob/master/examples/train_mnist.py

* split train/test by user id. 
    * Test - only last trip. 
    
* Try multiclass models

* Try tabnet models (tabular with attention)
    * + Lag feats
    * Note - the embedding here is not aware that the same IDs are the same (unlike TF's )! 

In [31]:
# from pytorch_tabnet.tab_model import TabNetClassifier
# from pytorch_tabnet.pretraining import TabNetPretrainer
# import torch
from sklearn.preprocessing import LabelEncoder
from sklearn.metrics import roc_auc_score

import pandas as pd
import numpy as np
np.random.seed(0)

* cat_idxs : list of int (default=[] - Mandatory for embeddings)
    * List of categorical features indices.

* cat_dims : list of int (default=[] - Mandatory for embeddings)

    * List of categorical features number of modalities (number of unique values for a categorical feature) /!\ no new modalities can be predicted

* cat_emb_dim : list of int (optional)

    * List of embeddings size for each categorical features. (default =1)
    
    
    
All the categorical vals must be known from train (demo used label encoder). Consider doing so also here at late step, to avoid unknown vals ? 

In [32]:
print(CAT_FEAT_NAMES)

['booker_country', 'device_class', 'affiliate_id', 'city_id', 'hotel_country', 'utrip_id', 'checkin_week', 'lag1_city_id', 'lag1_booker_country', 'lag1_hotel_country', 'lag1_affiliate_id', 'lag1_device_class', 'lag2_city_id', 'lag2_booker_country', 'lag2_hotel_country', 'lag2_affiliate_id', 'lag2_device_class', 'first_hotel_country', 'first_city_id']


In [33]:
NUMERIC_COLS = [item for item in list(df_feat.columns.drop(TARGET_COL))  if item not in CAT_FEAT_NAMES]
print(len(NUMERIC_COLS))
print("numeric cols",NUMERIC_COLS)

# for c in NUMERIC_COLS:
#     l_enc =   StandardScaler() # MinMaxScaler()#
#     l_enc.fit(df_feat[c].values.reshape(-1,1))
#     X_train[c] = l_enc.transform(X_train[c].values.reshape(-1,1))
#     X_test[c] = l_enc.transform(X_test[c].values.reshape(-1,1))


# l_enc =   StandardScaler() # MinMaxScaler()#
# l_enc.fit(df_feat[NUMERIC_COLS])
# X_train[NUMERIC_COLS] = l_enc.transform(X_train[NUMERIC_COLS])
# X_test[NUMERIC_COLS] = l_enc.transform(X_test[NUMERIC_COLS])

60
numeric cols ['rank', 'duration', 'checkin_day', 'checkin_weekday', 'checkin_month', 'checkin_year', 'checkin_day_of_year', 'checkin_quarter', 'checkout_weekday', 'checkout_week', 'checkout_day', 'checkin_month_sin', 'checkin_month_cos', 'checkin_week_sin', 'checkin_week_cos', 'row_num', 'total_rows', 'last', 'first_duration', 'first_same_country', 'affiliate_id_count', 'checkin_month_count', 'checkin_week_count', 'affiliate_id_nunique', 'booker_country_nunique', 'checkin_month_rank_by_booker_country', 'checkin_month_rank_by_affiliate', 'lag1_duration', 'lag1_same_country', 'lag1_checkin_weekday', 'lag1_checkin_week', 'lag1_checkout_weekday', 'lag1_city_id_count', 'lag1_affiliate_id_count', 'lag1_hotel_country_count', 'lag1_checkin_week_count', 'lag1_city_id_rank_by_hotel_country', 'lag1_city_id_rank_by_booker_country', 'lag1_city_id_rank_by_affiliate', 'lag1_affiliate_id_rank_by_hotel_country', 'lag1_hotel_country_rank_by_booker_country', 'lag1_hotel_country_rank_by_affiliate', 'la

In [34]:
# OBJECT_COLS = list(df_feat.select_dtypes("O").columns)
# df_feat[OBJECT_COLS] = df_feat[OBJECT_COLS].fillna("")
X_train[OBJECT_COLS] = X_train[OBJECT_COLS].fillna("")
X_test[OBJECT_COLS] = X_test[OBJECT_COLS].fillna("")

In [35]:
# df_feat[CAT_FEAT_NAMES] = df_feat[CAT_FEAT_NAMES].fillna(-1)
X_train[CAT_FEAT_NAMES] = X_train[CAT_FEAT_NAMES].fillna(-1)
X_test[CAT_FEAT_NAMES] = X_test[CAT_FEAT_NAMES].fillna(-1)

Ordinal/categoircals encoder

In [36]:

#### for now - cheat and fit on df_feat = all possible categoircals. In test, need to check that there won't be unk values +- update sklearn version

# for c in CAT_FEAT_NAMES:
#     l_enc = LabelEncoder().fit(df_feat[c])
#     X_train[c] = l_enc.transform(X_train[c])
#     X_test[c] = l_enc.transform(X_test[c])
#### https://scikit-learn.org/stable/modules/generated/sklearn.preprocessing.OrdinalEncoder.html

# # cat_encoder = OrdinalEncoder(handle_unknown="use_encoded_value",unknown_value="")
# cat_encoder = OrdinalEncoder()
# # X_train[CAT_FEAT_NAMES] = cat_encoder.fit_transform(X_train[CAT_FEAT_NAMES])
# cat_encoder.fit(df_feat[CAT_FEAT_NAMES])
# X_train[CAT_FEAT_NAMES] = cat_encoder.transform(X_train[CAT_FEAT_NAMES])
# X_test[CAT_FEAT_NAMES] = cat_encoder.transform(X_test[CAT_FEAT_NAMES])

In [37]:
# X_train.columns.get_loc(CAT_FEAT_NAMES)
cat_idxs = [X_train.columns.get_loc(c) for c in CAT_FEAT_NAMES if c in X_train]
assert len(cat_idxs) == len(CAT_FEAT_NAMES)
print(cat_idxs)

[5, 3, 4, 2, 75, 0, 9, 35, 38, 39, 37, 36, 55, 58, 59, 57, 56, 24, 25]


In [38]:
# #### get nuniques and set embeding dimension per categorical
# ### note that we need to change here if we want a higher embedding dimension!

# nunique = X_train.nunique()
# types = X_train.dtypes

# # categorical_columns = []
# categorical_dims = [] #{}
# cat_embed_dims = []
# for i,col in enumerate(cat_idxs):
# #     print(i,col)
# #     c_uniques = X_train.iloc[:,col].nunique()
#     c_uniques = df_feat[CAT_FEAT_NAMES[i]].nunique() ## try to use original data, more nuniques? 
    
#     categorical_dims.append(c_uniques)
# #     if col == "user_id" :  cat_embed_dims.append(10) ## need to change to use names. user id may overfit
#     cat_embed_dims.append(min(100,c_uniques//2))   

In [39]:
assert X_test[CAT_FEAT_NAMES].isna().sum().max() == X_train[CAT_FEAT_NAMES].isna().sum().max() == 0

In [40]:
print("sum top4 total percentage:",y_train.value_counts(normalize=True)[0:4].sum().round(3))
y_train.value_counts(normalize=True).round(5)

sum top4 total percentage: 1.0


0    0.97705
1    0.02295
Name: label, dtype: float64

In [41]:
if RUN_TABNET:
    # TabNetPretrainer
    unsupervised_model = TabNetPretrainer(    
        n_d=32, n_a=32, n_steps=4,
        cat_idxs=cat_idxs,
       cat_dims=categorical_dims,
       cat_emb_dim=cat_embed_dims,
        optimizer_fn=torch.optim.Adam,
        optimizer_params=dict(lr=2e-2),
        mask_type='entmax', # "sparsemax"
        device_name="auto" #"auto" "cpu" 
    )

    unsupervised_model.fit(
        X_train=X_train.values,
#         eval_set=[X_test.values],
        pretraining_ratio=0.35,
         max_epochs=6,
        batch_size = 512 ,# 1024 default , ~256-512 with GPU
    )
    
    ## save unsup model
    ### https://github.com/dreamquark-ai/tabnet/blob/develop/pretraining_example.ipynb
#     unsupervised_model.save_model('./.4_pretrain')


In [42]:
from __future__ import print_function, absolute_import

# from pytorch_tabnet.metrics import Metric
# from sklearn.metrics import top_k_accuracy_score


__all__ = ['accuracy']

def accuracy_k(output, target, topk=(4,)): # (1,))
    """Computes the precision@k for the specified values of k"""
    maxk = max(topk)
    batch_size = target.size(0)

    _, pred = output.topk(maxk, 1, True, True)
    pred = pred.t()
    correct = pred.eq(target.view(1, -1).expand_as(pred))

    res = []
    for k in topk:
        correct_k = correct[:k].view(-1).float().sum(0)
        res.append(correct_k.mul_(100.0 / batch_size))
    return res

In [43]:
if RUN_TABNET:
    clf = TabNetClassifier(    
        n_d=32, n_a=32, n_steps=4,
        cat_idxs=cat_idxs,
       cat_dims=categorical_dims,
       cat_emb_dim=cat_embed_dims,   
       optimizer_fn=torch.optim.Adam,
       optimizer_params=dict(lr=2e-2),
       scheduler_params={"step_size":50, # how to use learning rate scheduler
                         "gamma":0.9},
       scheduler_fn=torch.optim.lr_scheduler.StepLR,
#        mask_type='entmax', # "sparsemax"
        device_name="auto" #"auto" "cpu"
    )

    clf.fit(
        X_train=X_train.values, y_train=y_train.values,
        eval_set=[(X_train.values, y_train.values), (X_test.values, y_test.values)],
    #      eval_set=[(X_test.values, y_test.values)],
        eval_name=['train','test'],
        eval_metric=['accuracy'], # 'accuracy',
         max_epochs=max_epochs, 
        batch_size = 512 ,# 1024 default , ~256-512 with GPU
        from_unsupervised=unsupervised_model,    
    )

#     clf.save_model('./.full_tabnet_1192class')

#### feature importance & evaluation
* Look for leaks!
* May be bug with ordering of results - evaluation doesn't make sense. Note that diff # outputs/classes, likely culprit

In [44]:
if RUN_TABNET:
    ## top features (unsorted) - booker country
    # X_train.columns[clf.feature_importances_>1e-7]
    feat_imp = pd.DataFrame([X_train.columns,clf.feature_importances_]).T
    feat_imp = feat_imp.loc[feat_imp[1]>0].sort_values(1,ascending=False).reset_index(drop=True)
    feat_imp

In [45]:
# print(feat_imp[0].values)
# ['lag2_city_id' 'lag1_booker_country' 'lag2_booker_country'
#  'lag2_hotel_country' 'lag1_city_id' 'first_hotel_country'
#  'lag1_device_class' 'device_class' 'lag2_device_class' 'booker_country'
#  'lag1_hotel_country_rank_by_booker_country' 'checkin_week'
#  'lag1_city_id_count' 'checkin_quarter'
#  'lag2_booker_country_rank_by_booker_country' 'lag1_affiliate_id_count'
#  'lag1_checkin_month_rank_by_affiliate'
#  'lag2_checkin_month_rank_by_hotel_country' 'checkin_month_sin'
#  'lag2_hotel_country_count' 'lag2_checkin_month_count'
#  'lag2_affiliate_id_rank_by_booker_country' 'lag2_city_id_nunique']

# Catboost Classifciation/Ranking model
* +- add embeddings from lightfm, more features etc' 

* Catboost has ranking models. And supports embedding features. And taking time into account.
    * Example catboost ranking models/objectives: https://catboost.ai/docs/concepts/loss-functions-ranking.html
    * We could put in previous positive places visited in a trip as "weak positives" (e.g. "0.5 score" or a relative score based on distance/steps from final destination) 

In [46]:
X_train[CAT_FEAT_NAMES] = X_train[CAT_FEAT_NAMES].apply(pd.to_numeric, errors='ignore',downcast="integer")
X_test[CAT_FEAT_NAMES] = X_test[CAT_FEAT_NAMES].apply(pd.to_numeric, errors='ignore',downcast="integer")
X_train[CAT_FEAT_NAMES].dtypes

booker_country         object
device_class           object
affiliate_id            int16
city_id                 int32
hotel_country          object
utrip_id               object
checkin_week             int8
lag1_city_id            int32
lag1_booker_country    object
lag1_hotel_country     object
lag1_affiliate_id       int16
lag1_device_class      object
lag2_city_id            int32
lag2_booker_country    object
lag2_hotel_country     object
lag2_affiliate_id       int16
lag2_device_class      object
first_hotel_country    object
first_city_id           int32
dtype: object

In [47]:
print("train rows",X_train.shape[0])
print("test rows",X_test.shape[0])

train rows 1147004
test rows 286169


In [48]:
del df_feat
gc.collect()

197

In [49]:
def top4_accuracy(model):
    """warning - very hacky! - set to use global X_test, y_test variables"""
    y_test_pred = model.predict(X_test,prediction_type="Probability")[:,1]

    test_preds = pd.DataFrame({"y_test_pred":y_test_pred,
                               "candidate_city_id":X_test["city_id"],
                               "utrip_id":X_test["utrip_id"],
                               "label":y_test
                              })
    test_preds.sort_values(["utrip_id","y_test_pred"],inplace=True,ascending=False)
    res = 100*test_preds.groupby("utrip_id").head(4)["label"].sum() / test_preds["utrip_id"].nunique()
    print("Top 4 Accuracy: {0:.4f}".format(res))
    return res

## Catboost model

* golden feat https://catboost.ai/docs/concepts/python-reference_parameters-list.html#python-reference_parameters-list

In [50]:
%%time
train_pool = Pool(data=X_train,label = y_train,cat_features=CAT_FEAT_NAMES
                 ,group_id=X_train["utrip_id"]
                 )
test_pool = Pool(data=X_test,label = y_test,cat_features=CAT_FEAT_NAMES
                ,group_id=X_test["utrip_id"]
                )

CPU times: user 15.4 s, sys: 107 ms, total: 15.5 s
Wall time: 14.8 s


In [51]:

# https://colab.research.google.com/github/catboost/tutorials/blob/master/ranking/ranking_tutorial.ipynb#scrollTo=PC-BWnUscjHB

default_parameters = {
    'iterations': max_epochs,
    'custom_metric': ['AUC:type=Ranking', 'RecallAt:top=4'],
    'verbose': False,
    'random_seed': 0,
    "metric_period":50,
    "task_type":"GPU",
#     'loss_function': "PairLogit", # "PairLogitPairwise"
#     "ignored_features":["utrip_id"],
}

parameters = {}

parameters = deepcopy(default_parameters)

### parameter grid for grid search / Hyperparameter tuning:
hyper_params = {'depth':[3,6,8,10],
#           'learning_rate':[0.03,0.001,0.01,0.1,0.2,0.3], 
          'l2_leaf_reg':[3,1,5,10],
        #   'border_count':[32,10,50,100,200], ## we may want to set city ID as golden features
#           'ctr_border_count':[50,5,10,20,100,200],
#          'loss_function':["PairLogit", "PairLogitPairwise","YetiRank"], # not supported in grid search :()
         }

In [52]:
def fit_cbr_model(loss_function, additional_params=None, train_pool=train_pool, test_pool=test_pool,CV=True):
    """
    Fit catboost ranking model, or CV (cross validate) and return scores ; with a given loss function
    https://colab.research.google.com/github/catboost/tutorials/blob/master/ranking/ranking_tutorial.ipynb#scrollTo=RVNW0nowbtxH
    >>>model = fit_model('PairLogit', {'custom_metric': ['PrecisionAt:top=10', 'RecallAt:top=4']})
    
    """
    parameters = deepcopy(default_parameters)
    parameters['loss_function'] = loss_function
    parameters['train_dir'] = loss_function
    
    if additional_params is not None:
        parameters.update(additional_params)
         
    if CV:
        scores = cv(train_pool,params=parameters, plot=True)
#         print(scores)
        ## train model to get hacky top4 accuracy
        model = CatBoost(parameters)
        model.fit(train_pool, eval_set=test_pool, plot=False) 
        print()
        top4_acc = top4_accuracy(model)
        return scores
    else:
        model = CatBoost(parameters)
        model.fit(train_pool, eval_set=test_pool, plot=True) 
    
        return model

In [52]:
%%time
fit_cbr_model("PairLogit")

# Top 4 Accuracy: 58.1335
# test-RecallAt:top=4-mean: 0.64
# train-RecallAt:top=4-mean: 0.65

# CPU times: user 7min 30s, sys: 2min 22s, total: 9min 53s
# Wall time: 7min 29s

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

Metric RecallAt:top=4 is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric RecallAt:top=4 is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric RecallAt:top=4 is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric RecallAt:top=4 is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric RecallAt:top=4 is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric RecallAt:top=4 is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric RecallAt:top=4 is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric RecallAt:top=4 is not implemented on GPU. Will use CPU for metric com


Top 4 Accuracy: 58.1335
CPU times: user 7min 30s, sys: 2min 22s, total: 9min 53s
Wall time: 7min 29s


iterations  test-PairLogit-mean  test-PairLogit-std  train-PairLogit-mean  \
0            0             0.681205            0.004114              0.678151   
1           50             0.465969            0.002092              0.382545   
2          100             0.388649            0.011086              0.326751   
3          150             0.335585            0.010523              0.303870   
4          200             0.317865            0.009503              0.291993   
5          250             0.307280            0.006079              0.285274   
6          300             0.300430            0.004378              0.280186   
7          350             0.295912            0.004156              0.276058   
8          400             0.292430            0.003525              0.272472   
9          450             0.290317            0.003741              0.270159   
10         500             0.288531            0.004021              0.268092   
11         550             0.286940            0.004171              0.266140   
12         600             0.285304            0.003984              0.264036   
13         650             0.283920            0.004120              0.262415   
14         700             0.282703            0.004024              0.260989   
15         750             0.281548            0.003952              0.259555   
16         799             0.280603            0.004217              0.258362   

    train-PairLogit-std  test-AUC:type=Ranking-mean  \
0              0.000140                    0.720692   
1              0.001941                    0.819280   
2              0.001990                    0.841248   
3              0.002287                    0.864322   
4              0.003045                    0.871461   
5              0.002211                    0.876027   
6              0.001683                    0.878610   
7              0.001338                    0.880201   
8              0.001059                    0.881371   
9              0.001315                    0.882047   
10             0.001652                    0.882535   
11             0.001780                    0.882862   
12             0.001635                    0.883324   
13             0.001911                    0.883605   
14             0.001797                    0.883822   
15             0.001718                    0.884110   
16             0.001854                    0.884231   

    test-AUC:type=Ranking-std  test-RecallAt:top=4-mean  \
0                    0.002501                  0.057062   
1                    0.002471                  0.521653   
2                    0.007854                  0.521653   
3                    0.004224                  0.596948   
4                    0.004538                  0.609485   
5                    0.003013                  0.617330   
6                    0.001718                  0.622989   
7                    0.001148                  0.626679   
8                    0.000804                  0.629544   
9                    0.001155                  0.631980   
10                   0.001074                  0.633485   
11                   0.001211                  0.635777   
12                   0.001364                  0.637461   
13                   0.001528                  0.638858   
14                   0.001546                  0.640721   
15                   0.001491                  0.641795   
16                   0.001518                  0.642118   

    test-RecallAt:top=4-std  train-RecallAt:top=4-mean  \
0                  0.001778                   0.057062   
1                  0.002518                   0.607873   
2                  0.002518                   0.607873   
3                  0.000727                   0.610184   
4                  0.003935                   0.619443   
5                  0.002443                   0.627736   
6                  0.002895                   0.631712   
7                  0.003438

In [53]:
%%time
fit_cbr_model("PairLogitPairwise")

# Top 4 Accuracy: 54.5441
# test-RecallAt:top=4-mean: 0.55
# train-RecallAt:top=4-mean: 0.65
# CPU times: user 3min 24s, sys: 2min 36s, total: 6min 1s
# Wall time: 3min 16s

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

Metric RecallAt:top=4 is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric RecallAt:top=4 is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric RecallAt:top=4 is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric RecallAt:top=4 is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric RecallAt:top=4 is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric RecallAt:top=4 is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric RecallAt:top=4 is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric RecallAt:top=4 is not implemented on GPU. Will use CPU for metric com


Top 4 Accuracy: 54.5441
CPU times: user 3min 24s, sys: 2min 36s, total: 6min 1s
Wall time: 3min 16s


iterations  test-PairLogit-mean  test-PairLogit-std  train-PairLogit-mean  \
0            0             0.680401            0.000065              0.676929   
1           50             0.423635            0.001979              0.364262   
2          100             0.369338            0.004405              0.302977   
3          150             0.357422            0.003370              0.283101   
4          200             0.354596            0.003356              0.274244   
5          250             0.352383            0.005074              0.267531   
6          300             0.353311            0.006080              0.262842   
7          350             0.354928            0.006837              0.258672   
8          400             0.356264            0.006767              0.254926   
9          450             0.356053            0.005982              0.250997   
10         500             0.355091            0.005590              0.247249   
11         550             0.354878            0.006475              0.243865   
12         600             0.353845            0.006418              0.240640   
13         650             0.353275            0.006732              0.237766   
14         700             0.353930            0.007072              0.235227   
15         750             0.354666            0.008130              0.232769   
16         799             0.355069            0.008125              0.230471   

    train-PairLogit-std  test-AUC:type=Ranking-mean  \
0              0.000024                    0.794460   
1              0.000463                    0.837174   
2              0.000498                    0.846878   
3              0.000399                    0.848349   
4              0.000326                    0.848000   
5              0.000114                    0.848128   
6              0.000456                    0.847049   
7              0.000365                    0.845744   
8              0.000614                    0.845078   
9              0.001101                    0.845008   
10             0.001120                    0.845233   
11             0.001291                    0.845351   
12             0.001313                    0.845586   
13             0.001218                    0.845666   
14             0.001184                    0.845203   
15             0.001008                    0.844839   
16             0.000984                    0.844646   

    test-AUC:type=Ranking-std  test-RecallAt:top=4-mean  \
0                    0.004566                  0.316085   
1                    0.004820                  0.480782   
2                    0.003592                  0.530643   
3                    0.002638                  0.531360   
4                    0.002595                  0.535516   
5                    0.002922                  0.535731   
6                    0.002974                  0.538095   
7                    0.002768                  0.539420   
8                    0.002343                  0.540996   
9                    0.001749                  0.544113   
10                   0.001369                  0.546620   
11                   0.001741                  0.549199   
12                   0.001530                  0.550990   
13                   0.001754                  0.553748   
14                   0.002002                  0.554644   
15                   0.002233                  0.556148   
16                   0.002017                  0.557008   

    test-RecallAt:top=4-std  train-RecallAt:top=4-mean  \
0                  0.226091                   0.404429   
1                  0.001135                   0.568202   
2                  0.029789                   0.588405   
3                  0.014507                   0.595605   
4                  0.004581                   0.603038   
5                  0.007029                   0.608590   
6                  0.005736                   0.616399   
7                  0.004732

In [54]:
%%time
fit_cbr_model("YetiRank") ## YetiRankPairwise - may be better, but slow

# Top 4 Accuracy: 53.4530
# CPU times: user 9min 26s, sys: 3min 52s, total: 13min 19s
# Wall time: 10min 42s
# test-RecallAt:top=4-mean: 0.63
# train-RecallAt:top=4-mean: .63

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

Metric PFound is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric PFound is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric RecallAt:top=4 is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric PFound is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric PFound is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric RecallAt:top=4 is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric PFound is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric PFound is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learni


Top 4 Accuracy: 53.4530
CPU times: user 9min 26s, sys: 3min 52s, total: 13min 19s
Wall time: 10min 42s


iterations  test-PFound-mean  test-PFound-std  test-AUC:type=Ranking-mean  \
0            0          0.223576         0.013779                    0.720692   
1           50          0.350355         0.002912                    0.749169   
2          100          0.417470         0.001840                    0.799094   
3          150          0.458801         0.001900                    0.826364   
4          200          0.459410         0.001707                    0.834172   
5          250          0.509542         0.004881                    0.837065   
6          300          0.514873         0.002383                    0.839832   
7          350          0.520538         0.002408                    0.842008   
8          400          0.526907         0.001659                    0.844383   
9          450          0.533969         0.002122                    0.846946   
10         500          0.543509         0.004304                    0.850466   
11         550          0.552867         0.005322                    0.854414   
12         600          0.565864         0.009832                    0.857365   
13         650          0.578655         0.004536                    0.860494   
14         700          0.590608         0.004512                    0.862752   
15         750          0.601615         0.004151                    0.864918   
16         799          0.603385         0.004600                    0.866040   

    test-AUC:type=Ranking-std  test-RecallAt:top=4-mean  \
0                    0.002501                  0.057062   
1                    0.001301                  0.521653   
2                    0.003563                  0.521653   
3                    0.002089                  0.521653   
4                    0.002473                  0.521653   
5                    0.003499                  0.521653   
6                    0.003915                  0.526167   
7                    0.003664                  0.536089   
8                    0.003254                  0.536841   
9                    0.003815                  0.538990   
10                   0.003970                  0.541820   
11                   0.003327                  0.553642   
12                   0.002874                  0.585343   
13                   0.002519                  0.629580   
14                   0.002551                  0.635025   
15                   0.001875                  0.637497   
16                   0.002037                  0.638643   

    test-RecallAt:top=4-std  train-RecallAt:top=4-mean  \
0                  0.001778                   0.057062   
1                  0.002518                   0.521653   
2                  0.002518                   0.607873   
3                  0.002518                   0.607873   
4                  0.002518                   0.607873   
5                  0.002518                   0.607873   
6                  0.009936                   0.611635   
7                  0.004459                   0.617187   
8                  0.003255                   0.619766   
9                  0.004811                   0.620733   
10                 0.005914                   0.621700   
11                 0.011482                   0.623742   
12                 0.027094                   0.627772   
13                 0.005090                   0.628703   
14                 0.006873                   0.633055   
15                 0.005984                   0.635025   
16                 0.006159                   0.635509   

    train-RecallAt:top=4-std  
0                   0.000889  
1                   0.001259  
2                   0.002464  
3                   0.002464  
4                   0.002464  
5                   0.002464  
6                   0.005099  
7                   0.001513  
8                   0.002287  
9                   0.001680  
10                  0.001100  
11                  0.002237  
12                  0.002916  
13 

In [55]:
%%time
fit_cbr_model("QuerySoftMax") ## may be slow ? 

# Top 4 Accuracy: 67.2362
# test-RecallAt:top=4-mean : 0.70
# train-RecallAt:top=4-mean : 0.68
# CPU times: user 24min 39s, sys: 6min 13s, total: 30min 53s
# Wall time: 25min 15s

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

Metric RecallAt:top=4 is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric RecallAt:top=4 is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric RecallAt:top=4 is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric RecallAt:top=4 is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric RecallAt:top=4 is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric RecallAt:top=4 is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric RecallAt:top=4 is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric RecallAt:top=4 is not implemented on GPU. Will use CPU for metric com


Top 4 Accuracy: 67.2362
CPU times: user 24min 39s, sys: 6min 13s, total: 30min 53s
Wall time: 25min 15s


iterations  test-QuerySoftMax-mean  test-QuerySoftMax-std  \
0            0                3.693732               0.000551   
1           50                2.689877               0.024840   
2          100                2.316377               0.008981   
3          150                2.231935               0.011517   
4          200                2.171050               0.022833   
5          250                2.083975               0.022727   
6          300                2.040074               0.009247   
7          350                2.018933               0.003273   
8          400                2.003402               0.015768   
9          450                1.992696               0.022726   
10         500                1.984110               0.025091   
11         550                1.979045               0.026804   
12         600                1.972345               0.025731   
13         650                1.966947               0.026847   
14         700                1.962582               0.025154   
15         750                1.957841               0.026703   
16         799                1.951281               0.024621   

    train-QuerySoftMax-mean  train-QuerySoftMax-std  \
0                  3.693735                0.000276   
1                  2.703698                0.008108   
2                  2.333944                0.012313   
3                  2.248327                0.009521   
4                  2.190092                0.006588   
5                  2.114509                0.004244   
6                  2.075267                0.010008   
7                  2.055512                0.019933   
8                  2.041017                0.029119   
9                  2.030667                0.034245   
10                 2.022182                0.036194   
11                 2.016906                0.037716   
12                 2.009913                0.038064   
13                 2.004649                0.039982   
14                 2.000284                0.039488   
15                 1.995652                0.041653   
16                 1.989186                0.040471   

    test-AUC:type=Ranking-mean  test-AUC:type=Ranking-std  \
0                     0.545718                   0.001266   
1                     0.838276                   0.012595   
2                     0.876832                   0.002328   
3                     0.878701                   0.002359   
4                     0.882582                   0.002747   
5                     0.886435                   0.002135   
6                     0.888063                   0.001643   
7                     0.888871                   0.001918   
8                     0.889399                   0.001878   
9                     0.889969                   0.001460   
10                    0.890473                   0.001231   
11                    0.890723                   0.001131   
12                    0.891079                   0.001119   
13                    0.891416                   0.001286   
14                    0.891529                   0.001259   
15                    0.891699                   0.001473   
16                    0.892059                   0.001484   

    test-RecallAt:top=4-mean  test-RecallAt:top=4-std  \
0                   0.143282                 0.002229   
1                   0.607909                 0.004972   
2                   0.609055                 0.006529   
3                   0.614679                 0.005144   
4                   0.638285                 0.017039   
5                   0.683204                 0.007742   
6                   0.691944                 0.002482   
7                   0.693735                 0.004086   
8                   0.695634                 0.003779   
9                   0.698069                 0.002351   
10                  0.699896                 0.001337   
11                  0.701222                 0.001944   
12

In [56]:
%%time
fit_cbr_model("YetiRankPairwise")

# Top 4 Accuracy: 56.0373
# test-RecallAt:top=4-mean: 0.57
# train-RecallAt:top=4-mean: 0.65

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

Metric PFound is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric PFound is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric RecallAt:top=4 is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric PFound is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric PFound is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric RecallAt:top=4 is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric PFound is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learning time
Metric PFound is not implemented on GPU. Will use CPU for metric computation, this could significantly affect learni


Top 4 Accuracy: 56.0373


iterations  test-PFound-mean  test-PFound-std  test-AUC:type=Ranking-mean  \
0            0          0.322735         0.079769                    0.796052   
1           50          0.530950         0.022567                    0.853675   
2          100          0.551608         0.002142                    0.858991   
3          150          0.555847         0.001970                    0.858444   
4          200          0.557107         0.001943                    0.858230   
5          250          0.558915         0.004403                    0.858930   
6          300          0.559137         0.005160                    0.859215   
7          350          0.558567         0.004719                    0.859296   
8          400          0.557470         0.006132                    0.859406   
9          450          0.556743         0.005637                    0.859513   
10         500          0.556882         0.004991                    0.859542   
11         550          0.557385         0.004375                    0.859708   
12         600          0.557556         0.004837                    0.859628   
13         650          0.558013         0.005858                    0.859724   
14         700          0.557857         0.006989                    0.859636   
15         750          0.557549         0.006076                    0.859405   
16         799          0.558028         0.005928                    0.859361   

    test-AUC:type=Ranking-std  test-RecallAt:top=4-mean  \
0                    0.001121                  0.319631   
1                    0.002139                  0.538596   
2                    0.001087                  0.556184   
3                    0.000873                  0.564566   
4                    0.001119                  0.568327   
5                    0.001620                  0.570691   
6                    0.001203                  0.571085   
7                    0.001373                  0.571085   
8                    0.001258                  0.571085   
9                    0.001224                  0.569151   
10                   0.000937                  0.569008   
11                   0.000983                  0.571300   
12                   0.001092                  0.571014   
13                   0.001094                  0.572232   
14                   0.001167                  0.572303   
15                   0.000902                  0.571838   
16                   0.000877                  0.573127   

    test-RecallAt:top=4-std  train-RecallAt:top=4-mean  \
0                  0.226649                   0.404464   
1                  0.004606                   0.571050   
2                  0.003797                   0.589372   
3                  0.003625                   0.599312   
4                  0.004219                   0.607855   
5                  0.006173                   0.614357   
6                  0.008967                   0.620196   
7                  0.008290                   0.625139   
8                  0.010423                   0.629169   
9                  0.010120                   0.632858   
10                 0.007942                   0.636888   
11                 0.008869                   0.640595   
12                 0.008739                   0.643748   
13                 0.009858                   0.647312   
14                 0.010954                   0.649783   
15                 0.008846                   0.652452   
16                 0.009003                   0.655228   

    train-RecallAt:top=4-std  
0                   0.227316  
1                   0.003446  
2                   0.001936  
3                   0.001440  
4                   0.001478  
5                   0.002168  
6                   0.000763  
7                   0.002134  
8                   0.001185  
9                   0.000930  
10                  0.001632  
11                  0.002290  
12                  0.002718  
13 

In [57]:
# fit_cbr_model("Logloss") ##error - Stratified split is incompatible with groupwise metrics - rerun as classification (without group_ids) 

### Hyperparameter search 
* Run in pipeline on subset/sample of data
* CatBoostError: Parameter 'loss_function' currently is not supported in grid search :(

In [53]:
# model = CatBoost(parameters)
# # model = CatBoost(hyper_params)
# grid_search_result = model.grid_search(hyper_params, train_pool, verbose=0)

# print(grid_search_result)

In [54]:
# print(grid_search_result['params'])
# {'border_count': 32, 'depth': 6, 'l2_leaf_reg': 3}

In [60]:
%%time
### Normal classifier (not ranking) :
model = CatBoostClassifier(verbose=False,iterations=max_epochs, eval_metric='AUC', task_type="GPU",
                           metric_period=30,
                          ignored_features=["utrip_id"])
model.fit(train_pool,  eval_set=test_pool, plot=True,silent=False,use_best_model=True,
         )
print(model.get_best_score())
print()
top4_acc = top4_accuracy(model)



# bestTest = 0.9061549306
# bestIteration = 799
# {'learn': {'Logloss': 0.04975058936150179, 'AUC': 0.9652304649353027}, 'validation': {'Logloss': 0.06744807045836551, 'AUC': 0.9061549305915833}}

# Top 4 Accuracy: 64.6231
# CPU times: user 2min 19s, sys: 40.7 s, total: 3min
# Wall time: 2min 17s

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

Learning rate set to 0.042912
0:	learn: 0.6111331	test: 0.5127393	best: 0.5127393 (0)	total: 236ms	remaining: 3m 8s
30:	learn: 0.6614749	test: 0.5729508	best: 0.5729508 (30)	total: 7.43s	remaining: 3m 4s
60:	learn: 0.8603909	test: 0.7937304	best: 0.7937304 (60)	total: 14.7s	remaining: 2m 57s
90:	learn: 0.9202251	test: 0.8601156	best: 0.8601156 (90)	total: 22.2s	remaining: 2m 53s
120:	learn: 0.9359181	test: 0.8807634	best: 0.8807634 (120)	total: 30.1s	remaining: 2m 49s
150:	learn: 0.9462079	test: 0.8847522	best: 0.8847522 (150)	total: 37.9s	remaining: 2m 42s
180:	learn: 0.9513701	test: 0.8820381	best: 0.8847522 (150)	total: 45.9s	remaining: 2m 37s
210:	learn: 0.9541184	test: 0.8832067	best: 0.8847522 (150)	total: 54.3s	remaining: 2m 31s
240:	learn: 0.9562531	test: 0.8861905	best: 0.8861905 (240)	total: 1m 2s	remaining: 2m 25s
270:	learn: 0.9575975	test: 0.8886899	best: 0.8886899 (270)	total: 1m 11s	remaining: 2m 18s
300:	learn: 0.9587052	test: 0.8894615	best: 0.8894615 (300)	total: 1m 1

#### train model

In [ ]:
# if FASTRUN: 
#     iters = 100
#     parameters["iterations"] = 200
# else:
#     iters = 3000
# # model = CatBoostClassifier(verbose=False,iterations=iters, eval_metric='AUC', task_type="GPU",
# #                            metric_period=40,
# #                           ignored_features=["utrip_id"])#,learning_rate=0.1,



# # model = CatBoostClassifier(verbose=False,iterations=iters, eval_metric='AUC:type=Ranking',# task_type="GPU",
# #                            metric_period=40,
# #                            loss_function="PairLogitPairwise", ##"PairLogitPairwise" "YetiRank" "PairLogitPairwise"
# #                           ignored_features=["utrip_id"])

# model.fit(train_pool,  eval_set=test_pool, plot=True,silent=False,use_best_model=True,
# #           save_snapshot=True
#          )
# print(model.get_best_score())

# print()
# top4_acc = top4_accuracy(model)

### Results
##### 200k sampled data, max 

1.2k epochs, default settings, 35% of ranked data:

    * {'learn': {'Logloss': 0.0585, 'AUC': 0.959}
    * 'validation': {'Logloss': 0.07554, 'AUC': 0.9168}}

## Feature importance - SHAP
* We don't want to wait too long/to calculate it over 40 million rows, so we could look at a sample. e.g. top ranked (rank <= 10 | label ==1)  , or fiorst few rows


In [1]:
%%time
explainer = shap.TreeExplainer(model)
sample_pool = Pool(data=X_test.head(100123),label = y_test.head(100123),cat_features=CAT_FEAT_NAMES)
shap_values = explainer.shap_values(test_pool)
# summarize the effects of all the features over all the data
shap.summary_plot(shap_values, X_test.head(100123))

NameError: ignored